In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
!pip install opencv-python-headless numpy torch torchvision



In [3]:
!pip install yolov8

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.8/41.8 kB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.4/88.4 kB 2.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 953.4/953.4 kB 17.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.2/139.2 kB 10.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 kB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.8/66.8 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 113.6/113.6 kB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.2/62.2 MB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 872.1/872.1 kB 34.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.5/12.5 MB 63.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 4.4 MB/s eta 0:00:00
   ━

In [4]:
!pip install deep-sort-realtime

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 19.5 MB/s eta 0:00:00


In [5]:
!pip install ultralytics opencv-python-headless deep-sort-realtime pytube


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 kB 2.4 MB/s eta 0:00:00


In [6]:
import os

# Create the directory if it does not exist
video_dir = './videos'
os.makedirs(video_dir, exist_ok=True)


In [ ]:
!pip install yt-dlp

import yt_dlp

def download_video(youtube_url, output_path='./videos'):
    ydl_opts = {
        'outtmpl': os.path.join(output_path, '%(title)s.%(ext)s'),
        'format': 'best'
    }
    with yt_dlp.YoutubeDL(ydl_opts) as ydl:
        ydl.download([youtube_url])


video_urls = [
    "https://www.youtube.com/watch?v=V9YDDpo9LWg",
]


os.makedirs('./videos', exist_ok=True)


for url in video_urls:
    download_video(url)


[youtube] Extracting URL: https://www.youtube.com/watch?v=V9YDDpo9LWg
[youtube] V9YDDpo9LWg: Downloading webpage
[youtube] V9YDDpo9LWg: Downloading ios player API JSON
[youtube] V9YDDpo9LWg: Downloading web creator player API JSON
[youtube] V9YDDpo9LWg: Downloading player 57c75fa4
[youtube] V9YDDpo9LWg: Downloading m3u8 information
[info] V9YDDpo9LWg: Downloading 1 format(s): 18
[download] Destination: ./videos/ABA Therapy： Daniel - Communication.mp4
[download] 100% of    7.52MiB in 00:00:00 at 22.59MiB/s  


In [ ]:
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Path to the directory containing the videos
video_dir = '/content/videos'

# Create the directory if it does not exist
os.makedirs(video_dir, exist_ok=True)

# Loop over each video file in the directory
for video_file in os.listdir(video_dir):
    if video_file.endswith('.mp4'):  # Ensure it's a video file
        cap = cv2.VideoCapture(os.path.join(video_dir, video_file))

        # Prepare to save output video
        output_file = os.path.join(video_dir, 'output_' + video_file)
        fourcc = cv2.VideoWriter_fourcc(*'mp4v')
        out = None

        frame_count = 0
        total_time = 0

        # Skip every n frames to process only 10 FPS if the original is higher
        skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

        while cap.isOpened():
            ret, frame = cap.read()
            if not ret:
                break

            # Skip frames to increase processing speed
            if frame_count % skip_frames != 0:
                frame_count += 1
                continue

            start_time = time.time()

            # Run YOLOv8 detection
            results = model(frame)
            detections = []

            # Extract bounding boxes and confidence scores for 'person' class
            for result in results[0].boxes.data.cpu().numpy():
                x_min, y_min, x_max, y_max, confidence, class_id = result
                if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                    detections.append([[x_min, y_min, x_max, y_max], confidence])

            # Update tracker with detections
            tracks = tracker.update_tracks(detections, frame=frame)

            # Draw bounding boxes and labels
            for track in tracks:
                if not track.is_confirmed():
                    continue
                track_id = track.track_id
                ltrb = track.to_ltrb()
                cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
                cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

            # Measure time taken for one frame
            processing_time = time.time() - start_time
            total_time += processing_time
            frame_count += 1

            # Save the frame to output video
            if out is None:
                out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
            out.write(frame)

        cap.release()
        out.release()

        # Calculate and print FPS
        if frame_count > 0:
            fps = frame_count / total_time
            print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")



0: 384x640 (no detections), 209.1ms
Speed: 2.3ms preprocess, 209.1ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 214.7ms
Speed: 2.3ms preprocess, 214.7ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 kite, 226.7ms
Speed: 2.9ms preprocess, 226.7ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 kite, 202.2ms
Speed: 2.2ms preprocess, 202.2ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 kite, 214.5ms
Speed: 2.1ms preprocess, 214.5ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 kite, 228.9ms
Speed: 2.1ms preprocess, 228.9ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 kite, 210.4ms
Speed: 2.1ms preprocess, 210.4ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 kite, 155.3ms
Speed: 4.3ms preproces

In [ ]:
from google.colab import files
import shutil


shutil.make_archive('processed_videos', 'zip', video_dir)


files.download('processed_videos.zip')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
!pip install yt-dlp

import yt_dlp

def download_video(youtube_url, output_path='./videos'):
    ydl_opts = {
        'outtmpl': os.path.join(output_path, '%(title)s.%(ext)s'),
        'format': 'best'
    }
    with yt_dlp.YoutubeDL(ydl_opts) as ydl:
        ydl.download([youtube_url])


video_urls = [
    "https://www.youtube.com/watch?v=JBoc3w5EKfI",
]


os.makedirs('./videos', exist_ok=True)


for url in video_urls:
    download_video(url)


[youtube] Extracting URL: https://www.youtube.com/watch?v=JBoc3w5EKfI
[youtube] JBoc3w5EKfI: Downloading webpage
[youtube] JBoc3w5EKfI: Downloading ios player API JSON
[youtube] JBoc3w5EKfI: Downloading web creator player API JSON
[youtube] JBoc3w5EKfI: Downloading m3u8 information
[info] JBoc3w5EKfI: Downloading 1 format(s): 18
[download] Destination: ./videos/Group Therapy for Autism Spectrum Disorder.mp4
[download] 100% of    3.85MiB in 00:00:00 at 14.01MiB/s  


In [7]:
!pip install yt-dlp

import yt_dlp

def download_video(youtube_url, output_path='./videos'):
    ydl_opts = {
        'outtmpl': os.path.join(output_path, '%(title)s.%(ext)s'),
        'format': 'best'
    }
    with yt_dlp.YoutubeDL(ydl_opts) as ydl:
        ydl.download([youtube_url])


video_urls = [
    "https://www.youtube.com/watch?v=V9YDDpo9LWg",
    "https://www.youtube.com/watch?v=JBoc3w5EKfI",
    "https://www.youtube.com/watch?v=aWV7UUMddCU",
    "https://www.youtube.com/watch?v=f6wqlpG9rd0",
    "https://www.youtube.com/watch?v=GNVTuLHdeSo",
    "https://www.youtube.com/watch?v=SWtmkjd45so",
    "https://www.youtube.com/watch?v=RzI6Ar5mu2Q",
    "https://www.youtube.com/watch?v=aulLej6Z6W8",
    "https://www.youtube.com/watch?v=7pN6ydLE4EQ",
    "https://www.youtube.com/watch?v=fEEelCgBkWA",
    "https://www.youtube.com/watch?v=ckZQbQwM3oU",
    "https://www.youtube.com/watch?v=E8Wgwg3F4X0",
    "https://www.youtube.com/watch?v=rvIPH4ccfpI",
    "https://www.youtube.com/watch?v=F6iqlW6ovZc",
    "https://www.youtube.com/watch?v=9qjk-Sq415s&list=PL5B0D2D5B4BFE92C1&index=6",
    "https://www.youtube.com/watch?v=DI25kGJis0w",
    "https://www.youtube.com/watch?v=rrLhFZG6iQY",
    "https://www.youtube.com/watch?v=RKOZbT0ftL4&t=1s",
    "https://www.youtube.com/watch?v=N7TBbWHB01E",
    "https://www.youtube.com/watch?v=1YqVEVbXQ1c"
]


os.makedirs('./videos', exist_ok=True)


for url in video_urls:
    download_video(url)


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 170.1/170.1 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 22.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.3/157.3 kB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 13.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.4/194.4 kB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 9.8 MB/s eta 0:00:00
[youtube] Extracting URL: https://www.youtube.com/watch?v=V9YDDpo9LWg
[youtube] V9YDDpo9LWg: Downloading webpage
[youtube] V9YDDpo9LWg: Downloading ios player API JSON
[youtube] V9YDDpo9LWg: Downloading web creator player API JSON
[youtube] V9YDDpo9LWg: Downloading player 5f8f5b0f
[youtube] V9YDDpo9LWg: Downloading m3u8 information
[info] V9YDDpo9LWg: Downloading 1 format(s): 18
[download] Destination: ./videos/ABA Therapy： Daniel - Communication.mp4
[download] 100% of    7.52MiB in 00:00:00 at 18.03MiB/s  
[youtube] Extra

[youtube:tab] PL5B0D2D5B4BFE92C1 page 1: Downloading API JSON


[youtube:tab] PL5B0D2D5B4BFE92C1 page 1: Downloading API JSON


[youtube:tab] PL5B0D2D5B4BFE92C1 page 1: Downloading API JSON


[youtube:tab] Playlist In The Son-Rise Program® Playroom for Autism: Downloading 6 items of 6
[download] Downloading item 1 of 6
[youtube] Extracting URL: https://www.youtube.com/watch?v=Hd9marUY5GQ
[youtube] Hd9marUY5GQ: Downloading webpage
[youtube] Hd9marUY5GQ: Downloading ios player API JSON
[youtube] Hd9marUY5GQ: Downloading web creator player API JSON
[youtube] Hd9marUY5GQ: Downloading m3u8 information
[info] Hd9marUY5GQ: Downloading 1 format(s): 18
[download] Destination: ./videos/Sep 4 SonRise Session, Daniel & Mom.mp4
[download] 100% of   21.01MiB in 00:00:02 at 8.02MiB/s   
[download] Downloading item 2 of 6
[youtube] Extracting URL: https://www.youtube.com/watch?v=81fShK4roew
[youtube] 81fShK4roew: Downloading webpage
[youtube] 81fShK4roew: Downloading ios player API JSON
[youtube] 81fShK4roew: Downloading web creator player API JSON
[youtube] 81fShK4roew: Downloading m3u8 information
[info] 81fShK4roew: Downloading 1 format(s): 18
[download] Destination: ./videos/Chantal&El

file 2

In [ ]:
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Group Therapy for Autism Spectrum Disorder.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")




0: 384x640 8 persons, 135.3ms
Speed: 5.3ms preprocess, 135.3ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 persons, 144.6ms
Speed: 3.1ms preprocess, 144.6ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 persons, 132.5ms
Speed: 2.5ms preprocess, 132.5ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 6 persons, 132.4ms
Speed: 4.3ms preprocess, 132.4ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 6 persons, 157.2ms
Speed: 2.0ms preprocess, 157.2ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 6 persons, 193.8ms
Speed: 3.9ms preprocess, 193.8ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 persons, 259.6ms
Speed: 2.1ms preprocess, 259.6ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 8 persons, 1 dog, 255.8ms
Speed: 2.1ms preprocess, 255.8ms inference, 1.7ms postproce

In [ ]:
from google.colab import files
import shutil


shutil.make_archive('processed_videos', 'zip', video_dir)


files.download('processed_videos.zip')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

flie 3

In [ ]:
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Play Therapy Session working on Feelings with Candy Land Game.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Play Therapy Session working on Feelings with Candy Land Game'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')


Streaming output truncated to the last 5000 lines.
Speed: 6.3ms preprocess, 182.1ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 169.1ms
Speed: 2.1ms preprocess, 169.1ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 166.7ms
Speed: 7.7ms preprocess, 166.7ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 167.8ms
Speed: 8.4ms preprocess, 167.8ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 201.1ms
Speed: 9.5ms preprocess, 201.1ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 169.5ms
Speed: 7.2ms preprocess, 169.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 169.8ms
Speed: 7.7ms preprocess, 169.8m

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 4

In [ ]:
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Discrete Trial Training.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Discrete Trial Training'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')


Streaming output truncated to the last 5000 lines.
Speed: 2.0ms preprocess, 280.6ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 cup, 3 chairs, 1 dining table, 1 tv, 265.4ms
Speed: 3.0ms preprocess, 265.4ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 cup, 3 chairs, 1 dining table, 191.4ms
Speed: 2.1ms preprocess, 191.4ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 cup, 3 chairs, 1 dining table, 183.1ms
Speed: 2.0ms preprocess, 183.1ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 cup, 3 chairs, 1 dining table, 190.3ms
Speed: 2.4ms preprocess, 190.3ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 cup, 3 chairs, 1 dining table, 212.7ms
Speed: 2.0ms preprocess, 212.7ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 cup, 3 cha

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 5

In [ ]:
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'ABA Therapy - Play.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'ABA Therapy - Play'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')



0: 384x640 (no detections), 149.9ms
Speed: 2.7ms preprocess, 149.9ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 137.3ms
Speed: 3.3ms preprocess, 137.3ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 kite, 140.9ms
Speed: 3.8ms preprocess, 140.9ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 132.7ms
Speed: 3.6ms preprocess, 132.7ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 145.7ms
Speed: 2.4ms preprocess, 145.7ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 138.1ms
Speed: 2.1ms preprocess, 138.1ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 130.7ms
Speed: 3.7ms preprocess, 130.7ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 143.3ms
Speed: 3.9ms preprocess, 14

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 6


In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Sensory Play at Home： Proprioceptive Games.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Sensory Play at Home： Proprioceptive Games'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')


shutil.make_archive('processed_videos', 'zip', video_dir)


files.download('processed_videos.zip')



0: 384x640 1 person, 136.4ms
Speed: 2.3ms preprocess, 136.4ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 133.0ms
Speed: 2.4ms preprocess, 133.0ms inference, 3.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 135.7ms
Speed: 2.5ms preprocess, 135.7ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 142.5ms
Speed: 3.0ms preprocess, 142.5ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 133.5ms
Speed: 3.6ms preprocess, 133.5ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 136.9ms
Speed: 2.5ms preprocess, 136.9ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 135.5ms
Speed: 4.6ms preprocess, 135.5ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 147.4ms
Speed: 2.4ms preprocess, 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 7

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'ABA Therapy - Learning about Animals.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'ABA Therapy - Learning about Animals'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')





0: 384x640 (no detections), 417.2ms
Speed: 2.8ms preprocess, 417.2ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 224.0ms
Speed: 3.9ms preprocess, 224.0ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 231.5ms
Speed: 3.9ms preprocess, 231.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 253.2ms
Speed: 3.2ms preprocess, 253.2ms inference, 2.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 449.8ms
Speed: 6.0ms preprocess, 449.8ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 241.9ms
Speed: 3.8ms preprocess, 241.9ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 259.9ms
Speed: 4.0ms preprocess, 259.9ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 257.3ms
Speed: 3.7ms prepr

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 8

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Matching.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Matching'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




0: 384x640 4 persons, 1 dining table, 226.3ms
Speed: 6.5ms preprocess, 226.3ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 5 persons, 1 chair, 1 dining table, 1 remote, 230.4ms
Speed: 3.1ms preprocess, 230.4ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 1 cake, 1 chair, 1 dining table, 225.9ms
Speed: 3.2ms preprocess, 225.9ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 215.2ms
Speed: 5.2ms preprocess, 215.2ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 1 dining table, 268.1ms
Speed: 3.2ms preprocess, 268.1ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 1 dining table, 267.6ms
Speed: 6.5ms preprocess, 267.6ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 278.9ms
Speed: 3.2ms preprocess, 278.9ms inference, 1.5ms postprocess per image at shap

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 9

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'ABA Autism Training - Chapter 1 - The Discrete Trial.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'ABA Autism Training - Chapter 1 - The Discrete Trial'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




Streaming output truncated to the last 5000 lines.
Speed: 3.6ms preprocess, 206.5ms inference, 1.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 3 books, 221.4ms
Speed: 3.7ms preprocess, 221.4ms inference, 1.6ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 3 books, 225.0ms
Speed: 3.9ms preprocess, 225.0ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 3 books, 213.2ms
Speed: 13.7ms preprocess, 213.2ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 3 books, 228.4ms
Speed: 4.3ms preprocess, 228.4ms inference, 1.4ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 3 books, 233.4ms
Speed: 3.7ms preprocess, 233.4ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 3 books, 228.1ms
Speed: 3.9ms preprocess, 228.1ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons,

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 10

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Preference Assessment with Toys： Multiple Stimulus without Replacement (MSWO).mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Preference Assessment with Toys： Multiple Stimulus without Replacement (MSWO)'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')



100%|██████████| 6.25M/6.25M [00:00<00:00, 101MB/s]



0: 384x640 (no detections), 191.1ms
Speed: 5.2ms preprocess, 191.1ms inference, 9.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 132.1ms
Speed: 3.0ms preprocess, 132.1ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 209.4ms
Speed: 2.1ms preprocess, 209.4ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 204.4ms
Speed: 2.1ms preprocess, 204.4ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 238.4ms
Speed: 2.1ms preprocess, 238.4ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 204.2ms
Speed: 2.1ms preprocess, 204.2ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 200.5ms
Speed: 2.1ms preprocess, 200.5ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 205.7ms
Speed: 3.7ms prepr

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 11

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'How to Do Play Therapy ： Building a Growth Mindset Role Play.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'How to Do Play Therapy ： Building a Growth Mindset Role Play'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




Streaming output truncated to the last 5000 lines.
Speed: 4.2ms preprocess, 194.5ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 166.3ms
Speed: 2.1ms preprocess, 166.3ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 180.1ms
Speed: 2.1ms preprocess, 180.1ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 251.0ms
Speed: 2.7ms preprocess, 251.0ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 251.3ms
Speed: 3.6ms preprocess, 251.3ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 247.7ms
Speed: 2.1ms preprocess, 247.7ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 263.8ms
Speed: 2.2ms preprocess, 263.8ms inference, 3.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 258.7ms
Speed: 2.1ms preprocess, 258.7ms inference, 1.5ms pos

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 12

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'MASS TRIAL (Gross motor imitation).mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'MASS TRIAL (Gross motor imitation)'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')






0: 384x640 (no detections), 142.3ms
Speed: 2.3ms preprocess, 142.3ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 141.4ms
Speed: 3.7ms preprocess, 141.4ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 132.3ms
Speed: 3.7ms preprocess, 132.3ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 150.3ms
Speed: 3.4ms preprocess, 150.3ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 135.0ms
Speed: 3.4ms preprocess, 135.0ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 132.4ms
Speed: 3.4ms preprocess, 132.4ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 131.7ms
Speed: 2.9ms preprocess, 131.7ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 148.5ms
Speed: 2.5ms prepr

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 13

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Augmentative and Alternative Communication AAC.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Augmentative and Alternative Communication AAC'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')






0: 384x640 2 persons, 1 refrigerator, 1 book, 148.3ms
Speed: 4.4ms preprocess, 148.3ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 refrigerator, 137.5ms
Speed: 2.9ms preprocess, 137.5ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 refrigerator, 1 book, 146.8ms
Speed: 2.0ms preprocess, 146.8ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3 books, 133.8ms
Speed: 2.1ms preprocess, 133.8ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 refrigerator, 1 book, 165.5ms
Speed: 2.0ms preprocess, 165.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 book, 181.5ms
Speed: 2.1ms preprocess, 181.5ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 book, 176.4ms
Speed: 2.3ms preprocess, 176.4ms inference, 1.1ms postprocess per image at shape (

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 14

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Exploring the Therapeutic Playroom.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Exploring the Therapeutic Playroom'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')






0: 384x640 2 persons, 1 clock, 219.4ms
Speed: 2.1ms preprocess, 219.4ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 cell phone, 1 clock, 220.7ms
Speed: 2.1ms preprocess, 220.7ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 bench, 1 chair, 1 clock, 221.9ms
Speed: 2.4ms preprocess, 221.9ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 bottle, 1 clock, 231.4ms
Speed: 2.3ms preprocess, 231.4ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 clock, 218.3ms
Speed: 2.2ms preprocess, 218.3ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 chair, 1 clock, 227.1ms
Speed: 2.3ms preprocess, 227.1ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3 chairs, 1 clock, 269.1ms
Speed: 2.2ms preprocess, 269.1ms inference, 3.3ms postprocess per image at 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 15

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Sep 4 SonRise Session, Daniel & Mom.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Sep 4 SonRise Session, Daniel & Mom'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




Streaming output truncated to the last 5000 lines.
Speed: 16.9ms preprocess, 219.3ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 243.3ms
Speed: 4.0ms preprocess, 243.3ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 223.6ms
Speed: 3.6ms preprocess, 223.6ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 221.9ms
Speed: 5.3ms preprocess, 221.9ms inference, 1.4ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 221.8ms
Speed: 3.9ms preprocess, 221.8ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 207.8ms
Speed: 8.0ms preprocess, 207.8ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 196.2ms
Speed: 3.6ms preprocess, 196.2ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 dining table, 296.6ms
Speed: 8.5ms preprocess, 296.

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 16

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Chantal&Elizabeth Sonrise Part2 of 3.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Chantal&Elizabeth Sonrise Part2 of 3'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')



100%|██████████| 6.25M/6.25M [00:00<00:00, 65.0MB/s]


Streaming output truncated to the last 5000 lines.
Speed: 6.5ms preprocess, 310.7ms inference, 1.9ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 3 persons, 1 bottle, 1 cup, 345.8ms
Speed: 3.8ms preprocess, 345.8ms inference, 1.8ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 bottle, 313.3ms
Speed: 3.4ms preprocess, 313.3ms inference, 3.9ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 bottle, 339.9ms
Speed: 8.1ms preprocess, 339.9ms inference, 1.6ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 bottle, 1 chair, 309.9ms
Speed: 5.8ms preprocess, 309.9ms inference, 1.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 cat, 1 bottle, 309.9ms
Speed: 12.7ms preprocess, 309.9ms inference, 1.6ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 cat, 1 bottle, 1 bowl, 1 chair, 312.3ms
Speed: 12.3ms preprocess, 312.3ms inference, 1.7ms postprocess per 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 17

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Jakob and Son Rise.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Jakob and Son Rise'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')





0: 480x640 3 persons, 291.3ms
Speed: 4.3ms preprocess, 291.3ms inference, 1.9ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 266.1ms
Speed: 3.5ms preprocess, 266.1ms inference, 1.9ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 4 persons, 1 bottle, 1 chair, 285.7ms
Speed: 4.3ms preprocess, 285.7ms inference, 1.8ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 3 persons, 285.8ms
Speed: 4.1ms preprocess, 285.8ms inference, 1.8ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 chair, 301.4ms
Speed: 3.6ms preprocess, 301.4ms inference, 2.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 3 persons, 205.0ms
Speed: 3.5ms preprocess, 205.0ms inference, 1.6ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 3 persons, 1 toilet, 1 refrigerator, 227.1ms
Speed: 3.2ms preprocess, 227.1ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 chair, 198.9ms
Spe

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 18

In [ ]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Sep 4 SonRise Session, Daniel & Dad.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Sep 4 SonRise Session, Daniel & Dad'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




Streaming output truncated to the last 5000 lines.
Speed: 4.7ms preprocess, 233.1ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 potted plant, 1 dining table, 231.5ms
Speed: 4.0ms preprocess, 231.5ms inference, 1.5ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 245.1ms
Speed: 3.7ms preprocess, 245.1ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 230.0ms
Speed: 10.2ms preprocess, 230.0ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 potted plant, 1 dining table, 220.1ms
Speed: 4.1ms preprocess, 220.1ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 potted plant, 1 dining table, 232.2ms
Speed: 3.6ms preprocess, 232.2ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 potted plant, 1 dining table, 239.5ms
Speed: 3.9ms preprocess, 239.5ms inference, 1.

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 19

In [1]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Speech Therapy Training Session- Moderate to Severe Autism.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Speech Therapy Training Session- Moderate to Severe Autism'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')


shutil.make_archive('processed_videos', 'zip', video_dir)


files.download('processed_videos.zip')


ModuleNotFoundError: No module named 'deep_sort_realtime'

In [7]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Jan 5 SonRise Mom part 1.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Jan 5 SonRise Mom part 1'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




100%|██████████| 6.25M/6.25M [00:00<00:00, 101MB/s]


Streaming output truncated to the last 5000 lines.
Speed: 4.3ms preprocess, 226.5ms inference, 1.5ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 chair, 225.9ms
Speed: 4.1ms preprocess, 225.9ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 227.9ms
Speed: 15.9ms preprocess, 227.9ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 210.9ms
Speed: 7.7ms preprocess, 210.9ms inference, 1.1ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 240.9ms
Speed: 4.2ms preprocess, 240.9ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 223.9ms
Speed: 4.6ms preprocess, 223.9ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 donut, 189.8ms
Speed: 5.0ms preprocess, 189.8ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 donut, 201.1ms
Speed: 11.6ms prep

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 20

In [8]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Heather playroom Jan 2008 1.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Heather playroom Jan 2008 1'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')





0: 480x640 2 persons, 179.8ms
Speed: 3.4ms preprocess, 179.8ms inference, 2.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 3 persons, 172.9ms
Speed: 4.8ms preprocess, 172.9ms inference, 1.4ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 person, 159.4ms
Speed: 3.5ms preprocess, 159.4ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 person, 1 cup, 1 cake, 1 dining table, 164.4ms
Speed: 4.9ms preprocess, 164.4ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 person, 1 dining table, 158.1ms
Speed: 4.4ms preprocess, 158.1ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 174.4ms
Speed: 4.7ms preprocess, 174.4ms inference, 1.4ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 1 dog, 194.0ms
Speed: 3.6ms preprocess, 194.0ms inference, 1.5ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 persons, 195.7ms
Speed: 3.4ms pr

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 21

In [9]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'ABA Therapy - Social Engagement.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'ABA Therapy - Social Engagement'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')





0: 384x640 (no detections), 158.3ms
Speed: 1.9ms preprocess, 158.3ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 144.6ms
Speed: 3.0ms preprocess, 144.6ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 130.3ms
Speed: 2.4ms preprocess, 130.3ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 139.0ms
Speed: 4.0ms preprocess, 139.0ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 135.5ms
Speed: 3.4ms preprocess, 135.5ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 136.8ms
Speed: 3.9ms preprocess, 136.8ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 165.7ms
Speed: 2.2ms preprocess, 165.7ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 132.5ms
Speed: 2.4ms prepr

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 22

In [10]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Incidental Teaching.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Incidental Teaching'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




Streaming output truncated to the last 5000 lines.
Speed: 8.3ms preprocess, 190.9ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5 cups, 1 chair, 2 couchs, 1 dining table, 1 book, 193.5ms
Speed: 2.0ms preprocess, 193.5ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5 cups, 1 chair, 2 couchs, 1 dining table, 1 book, 192.2ms
Speed: 2.2ms preprocess, 192.2ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5 cups, 1 chair, 2 couchs, 1 dining table, 1 book, 207.9ms
Speed: 2.5ms preprocess, 207.9ms inference, 2.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 7 cups, 1 chair, 2 couchs, 1 dining table, 1 book, 186.7ms
Speed: 7.2ms preprocess, 186.7ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 6 cups, 1 chair, 1 couch, 1 dining table, 1 book, 175.0ms
Speed: 2.1ms preprocess, 175.0ms inference, 1.2ms 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 23

In [11]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Autism (Moderate - Severe) and ABA - Training Session.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Autism (Moderate - Severe) and ABA - Training Session'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')





Streaming output truncated to the last 5000 lines.
Speed: 2.3ms preprocess, 191.2ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 4 chairs, 1 dining table, 1 book, 200.2ms
Speed: 2.4ms preprocess, 200.2ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 4 chairs, 1 dining table, 189.4ms
Speed: 2.6ms preprocess, 189.4ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 4 chairs, 1 dining table, 189.2ms
Speed: 2.5ms preprocess, 189.2ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 4 chairs, 1 dining table, 160.1ms
Speed: 2.0ms preprocess, 160.1ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4 chairs, 1 dining table, 179.5ms
Speed: 8.9ms preprocess, 179.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4 chairs, 1 dining table, 180.6ms
Speed: 2.5m

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 24

In [12]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Natural Environment Teaching (NET).mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Natural Environment Teaching (NET)'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')





0: 384x640 1 person, 2 cups, 1 bowl, 1 toilet, 1 refrigerator, 210.8ms
Speed: 3.1ms preprocess, 210.8ms inference, 3.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 cups, 1 bowl, 1 toilet, 206.7ms
Speed: 2.0ms preprocess, 206.7ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 cups, 1 bowl, 1 toilet, 1 refrigerator, 217.7ms
Speed: 2.1ms preprocess, 217.7ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 2 cups, 1 bowl, 1 toilet, 199.7ms
Speed: 2.3ms preprocess, 199.7ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 cup, 1 bowl, 1 toilet, 229.5ms
Speed: 2.1ms preprocess, 229.5ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 2 cups, 1 bowl, 1 toilet, 1 refrigerator, 242.2ms
Speed: 2.0ms preprocess, 242.2ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

file 25

In [8]:
from google.colab import files
import shutil
import cv2
import torch
from deep_sort_realtime.deepsort_tracker import DeepSort
import os
from ultralytics import YOLO
import time
from google.colab import files
import shutil

# Load YOLOv8 model (using the smallest and fastest model)
model = YOLO('yolov8n.pt')

# Initialize Deep SORT tracker
tracker = DeepSort(max_age=30, n_init=3)

# Directory containing the video files
video_dir = '/content/videos'

# Specify the video file you want to process
video_file = 'Speech Therapy Training Session- Moderate to Severe Autism.mp4'

# Check if the video file exists
video_path = os.path.join(video_dir, video_file)
if not os.path.exists(video_path):
    print(f"Video file {video_file} does not exist in {video_dir}.")
else:
    cap = cv2.VideoCapture(video_path)

    # Prepare to save output video
    output_file = os.path.join(video_dir, 'output_' + video_file)
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = None

    frame_count = 0
    total_time = 0

    # Skip every n frames to process only 10 FPS if the original is higher
    skip_frames = 6  # Skip frames for performance improvement (adjust as needed)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Skip frames to increase processing speed
        if frame_count % skip_frames != 0:
            frame_count += 1
            continue

        start_time = time.time()

        # Run YOLOv8 detection
        results = model(frame)
        detections = []

        # Extract bounding boxes and confidence scores for 'person' class
        for result in results[0].boxes.data.cpu().numpy():
            x_min, y_min, x_max, y_max, confidence, class_id = result
            if int(class_id) == 0:  # 'person' class id in COCO dataset is 0
                detections.append([[x_min, y_min, x_max, y_max], confidence])

        # Update tracker with detections
        tracks = tracker.update_tracks(detections, frame=frame)

        # Draw bounding boxes and labels
        for track in tracks:
            if not track.is_confirmed():
                continue
            track_id = track.track_id
            ltrb = track.to_ltrb()
            cv2.rectangle(frame, (int(ltrb[0]), int(ltrb[1])), (int(ltrb[2]), int(ltrb[3])), (0, 255, 0), 2)
            cv2.putText(frame, f'ID {track_id}', (int(ltrb[0]), int(ltrb[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

        # Measure time taken for one frame
        processing_time = time.time() - start_time
        total_time += processing_time
        frame_count += 1

        # Save the frame to output video
        if out is None:
            out = cv2.VideoWriter(output_file, fourcc, 20.0, (frame.shape[1], frame.shape[0]))
        out.write(frame)

    cap.release()
    out.release()

    # Calculate and print FPS
    if frame_count > 0:
        fps = frame_count / total_time
        print(f"Processed {video_file} at {fps:.2f} FPS in {total_time:.2f} seconds")

    # Create a zip archive with a custom name
    zip_file_name = 'Speech Therapy Training Session- Moderate to Severe Autism'
    shutil.make_archive(zip_file_name, 'zip', video_dir)

    # Download the zip file
    files.download(f'{zip_file_name}.zip')




100%|██████████| 6.25M/6.25M [00:00<00:00, 57.2MB/s]


Streaming output truncated to the last 5000 lines.
Speed: 2.0ms preprocess, 265.5ms inference, 2.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 1 chair, 1 remote, 1 book, 278.4ms
Speed: 5.1ms preprocess, 278.4ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 chair, 1 book, 283.4ms
Speed: 9.2ms preprocess, 283.4ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 chairs, 1 book, 283.9ms
Speed: 2.0ms preprocess, 283.9ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 persons, 2 chairs, 1 book, 293.7ms
Speed: 2.7ms preprocess, 293.7ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 1 chair, 1 book, 289.6ms
Speed: 2.1ms preprocess, 289.6ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 chairs, 1 book, 187.8ms
Speed: 3.0ms preprocess, 187.8ms inference, 1.5ms postproces

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>